In [13]:
import os
import folium
import PIL
from PIL import Image
import io
import base64
path=r'.\coord'
images= os.listdir(path)

In [14]:

Center_Of_Map_coordinates=(32.783135, 35.173470)
html = '<img src="data:image/jpg;base64,{}">'.format
# create map
m = folium.Map(location=[Center_Of_Map_coordinates[0],Center_Of_Map_coordinates[1]], zoom_start=16)
# add markers
for i in range(len(images)):
    coord=[float(c) for c in images[i][:-4].split(',')] # get coordinates from image name
    img = PIL.Image.open('/'.join([path,images[i]]))
    new_size=tuple(int(0.09 * elem) for elem in img.size) # resize image to fit popup window
    small_img=img.resize(new_size)
    buf = io.BytesIO()
    small_img.save(buf, format='JPEG')
    byte_im = buf.getvalue()
    encoded = base64.b64encode(byte_im).decode()
    iframe = folium.IFrame(html(encoded), width=new_size[1], height=new_size[0])
    popup = folium.Popup(iframe, max_width=new_size[1])
    folium.Marker(location=coord, popup=popup).add_to(m)  # add image popup to coordinate

m

In [ ]:
m.save('map with image markers.html')

# tests

In [21]:
from gmplot import GoogleMapPlotter
from random import random

# We subclass this just to change the map type
class CustomGoogleMapPlotter(GoogleMapPlotter):
    def __init__(self, center_lat, center_lng, zoom, apikey='',
                 map_type='satellite'):
        super().__init__(center_lat, center_lng, zoom, apikey)

        self.map_type = map_type
        assert(self.map_type in ['roadmap', 'satellite', 'hybrid', 'terrain'])

    def write_map(self,  f):
        f.write('\t\tvar centerlatlng = new google.maps.LatLng(%f, %f);\n' %
                (self.center[0], self.center[1]))
        f.write('\t\tvar myOptions = {\n')
        f.write('\t\t\tzoom: %d,\n' % (self.zoom))
        f.write('\t\t\tcenter: centerlatlng,\n')

        # This is the only line we change
        f.write('\t\t\tmapTypeId: \'{}\'\n'.format(self.map_type))


        f.write('\t\t};\n')
        f.write(
            '\t\tvar map = new google.maps.Map(document.getElementById("map_canvas"), myOptions);\n')
        f.write('\n')

initial_zoom = 16
num_pts = 40

lats = [37.428]
lons = [-122.145]
for pt in range(num_pts):
    lats.append(lats[-1] + (random() - 0.5)/100)
    lons.append(lons[-1] + random()/100)
gmap = CustomGoogleMapPlotter(lats[0], lons[0], initial_zoom,
                              map_type='satellite')
gmap.plot(lats, lons, 'cornflowerblue', edge_width=10)

gmap.draw("mymap.html")

In [22]:
gmap = CustomGoogleMapPlotter(Center_Of_Map_coordinates[0],Center_Of_Map_coordinates[1], initial_zoom,
                              map_type='satellite')
gmap.draw("mymap.html")